# Segmenting and Clustering Neighborhoods in Toronto

This notebook is intended for Capstone project week 3. 
In this assignment, we will explore, segment, and cluster the neighborhoods in the city of Toronto. We will collect the data from foursquare , make it in a structured format. Once the data is in a structured format, we will replicate the analysis that we did to the New York City dataset to explore and cluster the neighborhoods in the city of Toronto.

Before we download the data and start exploring it, let's download some dependencies needed by this notebook

In [41]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

/bin/bash: conda: command not found
Libraries imported.


## 1. Download and Explore Dataset

### 1.1. Prepare dataset when Toronto_Neighbourhood_Coordinate.csv is available in github account 'MariaTriagni'

If the Toronto_Neighbourhood_Coordinate.csv is available in github account 'MariaTriagni' ( https://github.com/MariaTriagni/Data/blob/master/Toronto_Neighbourhood_Coordinates.csv ) then all we need to do is just upload to dataframe

In [42]:
#If Toronto_Neighbourhood_Coordinate is exists already and it's available in github, load the csv from github to dataframe df_Toronto
import pandas as pd 

url = "https://raw.githubusercontent.com/MariaTriagni/Data/master/" + "Toronto_Neighbourhood_Coordinates.csv"
print(url)
df_Toronto = pd.read_csv(url) 

df_Toronto.head() 


https://raw.githubusercontent.com/MariaTriagni/Data/master/Toronto_Neighbourhood_Coordinates.csv


Postcode          Borough     Neighbourhood   latitude  longitude
0      M5R  Central Toronto         Yorkville  43.671386 -79.390168
1      M3J       North York   York University  43.779242 -79.483559
2      M2P       North York   York Mills West  43.744039 -79.406657
3      M2L       North York        York Mills  43.744039 -79.406657
4      M4C        East York  Woodbine Heights  43.699930 -79.319132

In [43]:
df_Toronto

Postcode           Borough  \
0        M5R   Central Toronto   
1        M3J        North York   
2        M2P        North York   
3        M2L        North York   
4        M4C         East York   
5        M4B         East York   
6        M1G       Scarborough   
7        M3H        North York   
8        M2R        North York   
9        M2N        North York   
10       M2M        North York   
11       M1P       Scarborough   
12       M1R       Scarborough   
13       M9N              York   
14       M9P         Etobicoke   
15       M1E       Scarborough   
16       M9B         Etobicoke   
17       M4A        North York   
18       M5L  Downtown Toronto   
19       M6L        North York   
20       M1X       Scarborough   
21       M5S  Downtown Toronto   
22       M5J  Downtown Toronto   
23       M5X  Downtown Toronto   
24       M6J      West Toronto   
25       M5J  Downtown Toronto   
26       M5K  Downtown Toronto   
27       M4H         East York   
28       M9V         Etobicoke   
29       M8Z         Etobicoke   
30       M8Y         Etobicoke   
31       M8X         Etobicoke   
32       M6P      West Toronto   
33       M6N              York   
34       M4K      East Toronto   
35       M4L      East Toronto   
36       M4E      East Toronto   
37       M5R   Central Toronto   
38       M1T       Scarborough   
39       M6S      West Toronto   
40       M8Y         Etobicoke   
41       M4V   Central Toronto   
42       M4T   Central Toronto   
43       M1T       Scarborough   
44       M4M      East Toronto   
45       M5W  Downtown Toronto   
46       M1V       Scarborough   
47       M9R         Etobicoke   
48       M5C  Downtown Toronto   
49       M4X  Downtown Toronto   
50       M9V         Etobicoke   
51       M8Z         Etobicoke   
52       M5V  Downtown Toronto   
53       M4V   Central Toronto   
54       M6M              York   
55       M9V         Etobicoke   
56       M2L        North York   
57       M1M       Scarborough   
58       M1J       Scarborough   
59       M1P       Scarborough   
60       M5B  Downtown Toronto   
61       M6N              York   
62       M6S      West Toronto   
63       M8Z         Etobicoke   
64       M8Y         Etobicoke   
65       M1C       Scarborough   
66       M1B       Scarborough   
67       M5N   Central Toronto   
68       M4W  Downtown Toronto   
69       M6R      West Toronto   
70       M4K      East Toronto   
71       M9R         Etobicoke   
72       M5H  Downtown Toronto   
73       M4V   Central Toronto   
74       M5V  Downtown Toronto   
75       M7A  Downtown Toronto   
76       M9B         Etobicoke   
77       M1C       Scarborough   
78       M3A        North York   
79       M4B         East York   
80       M6K      West Toronto   
81       M6R      West Toronto   
82       M2J        North York   
83       M8Y         Etobicoke   
84       M8X         Etobicoke   
85       M9C         Etobicoke   
86       M1L       Scarborough   
87       M1A      Not assigned   
88       M2A      Not assigned   
89       M8A      Not assigned   
90       M9A      Queen's Park   
91       M2B      Not assigned   
92       M7B      Not assigned   
93       M8B      Not assigned   
94       M2C      Not assigned   
95       M7C      Not assigned   
96       M8C      Not assigned   
97       M2E      Not assigned   
98       M3E      Not assigned   
99       M7E      Not assigned   
100      M8E      Not assigned   
101      M9E      Not assigned   
102      M2G      Not assigned   
103      M3G      Not assigned   
104      M7G      Not assigned   
105      M8G      Not assigned   
106      M9G      Not assigned   
107      M7H      Not assigned   
108      M8H      Not assigned   
109      M9H      Not assigned   
110      M7J      Not assigned   
111      M8J      Not assigned   
112      M9J      Not assigned   
113      M7K      Not assigned   
114      M8K      Not assigned   
115      M9K      Not assigned   
116      M7L      Not assi

### 1.2. Clean the dataset

In the dataset, we can see some neighbourhood doesn't have latitude and longitude and some postal code also doesn't have latitude and longitude. We will remove all the neighbourhood which doesn't have latitude and longitude.

In [0]:
#get the index list of the dataframe
#list(df_Toronto.index) 

In [45]:
# Get the list of indexes for which column latitude or longitude has value 0.0
indexNames = df_Toronto[ (df_Toronto['latitude'] == 0.0) | (df_Toronto['longitude'] == 0.0) ].index
 
# View the list of indexes indexNames
indexNames

Int64Index([ 45,  74,  87,  88,  89,  90,  91,  92,  93,  94,  95,  96,  97,
             98,  99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110,
            111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123,
            124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136,
            137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149,
            150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162,
            163, 164, 209, 213, 251, 266, 267, 269, 270, 272, 278],
           dtype='int64')

In [46]:
# Delete these row indexes from dataFrame
df_Toronto.drop(indexNames , inplace=True)
df_Toronto

Postcode           Borough             Neighbourhood   latitude  longitude
0        M5R   Central Toronto                 Yorkville  43.671386 -79.390168
1        M3J        North York           York University  43.779242 -79.483559
2        M2P        North York           York Mills West  43.744039 -79.406657
3        M2L        North York                York Mills  43.744039 -79.406657
4        M4C         East York          Woodbine Heights  43.699930 -79.319132
5        M4B         East York          Woodbine Gardens  43.712078 -79.302567
6        M1G       Scarborough                    Woburn  43.759824 -79.225291
7        M3H        North York            Wilson Heights  43.740519 -79.440017
8        M2R        North York           Willowdale West  43.761509 -79.410923
9        M2N        North York          Willowdale South  43.761509 -79.410923
10       M2M        North York                Willowdale  43.761509 -79.410923
11       M1P       Scarborough           Wexford Heights  43.743242 -79.304641
12       M1R       Scarborough                   Wexford  43.745377 -79.294716
13       M9N              York                    Weston  43.700161 -79.516247
14       M9P         Etobicoke                 Westmount  43.693640 -79.521043
15       M1E       Scarborough                 West Hill  43.768914 -79.187291
16       M9B         Etobicoke           West Deane Park  43.663199 -79.568568
17       M4A        North York          Victoria Village  43.732658 -79.311189
18       M5L  Downtown Toronto            Victoria Hotel  43.669469 -79.373268
19       M6L        North York               Upwood Park  43.708655 -79.502546
20       M1X       Scarborough               Upper Rouge  43.804930 -79.165837
21       M5S  Downtown Toronto     University of Toronto  43.663462 -79.397760
22       M5J  Downtown Toronto             Union Station  43.644693 -79.380132
23       M5X  Downtown Toronto          Underground city  43.770145 -79.374863
24       M6J      West Toronto                   Trinity  43.665302 -79.395252
25       M5J  Downtown Toronto           Toronto Islands  43.616196 -79.369358
26       M5K  Downtown Toronto   Toronto Dominion Centre  43.647377 -79.381372
27       M4H         East York          Thorncliffe Park  43.704553 -79.345407
28       M9V         Etobicoke               Thistletown  43.737266 -79.565317
29       M8Z         Etobicoke        The Queensway West  43.623618 -79.514764
30       M8Y         Etobicoke        The Queensway East  43.609309 -79.567732
31       M8X         Etobicoke              The Kingsway  43.647381 -79.511333
32       M6P      West Toronto        The Junction South  43.665478 -79.470352
33       M6N              York        The Junction North  43.665478 -79.470352
34       M4K      East Toronto         The Danforth West  43.686433 -79.300356
35       M4L      East Toronto          The Beaches West  43.671024 -79.296712
36       M4E      East Toronto               The Beaches  43.671024 -79.296712
37       M5R   Central Toronto                 The Annex  43.670338 -79.407117
38       M1T       Scarborough             Tam O'Shanter  43.781045 -79.298094
39       M6S      West Toronto                   Swansea  43.644940 -79.478313
40       M8Y         Etobicoke                  Sunnylea  43.641597 -79.501665
41       M4V   Central Toronto           Summerhill West  43.681678 -79.390504
42       M4T   Central Toronto           Summerhill East  43.681678 -79.390504
43       M1T       Scarborough                  Sullivan  43.772680 -79.315945
44       M4M      East Toronto           Studio District  43.644403 -79.387891
46       M1V       Scarborough              Steeles East  43.816178 -79.314538
47       M9R         Etobicoke              St. Phillips  43.700048 -79.543765
48       M5C  Downtown Toronto            St. James Town  43.669403 -79.372704
49       M4X  Downtown Toronto            St. James Town  43.669403 -79.372704
50       M9V         Etobicoke             South Steel

Now dataframe df_Toronto has clean data and ready for next step

## 2. Analyze the data set

In this section, we will use the Foursquare API to explore neighborhoods in Toronto city. We will use the explore function to get the most common venue categories in each neighborhood, and then use this feature to group the neighborhoods into clusters. We will use the k-means clustering algorithm to complete this task. Finally, we will use the Folium library to visualize the neighborhoods in Toronto city.

## 2.1 Create a map of Toronto with neighborhoods superimposed on top.

#### Use geopy library to get the latitude and longitude values of Toronto City.

In [47]:
address = 'Toronto City, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto City are 43.653963, -79.387207.


In [48]:
# create map of Toronto using latitude and longitude values
map_Toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_Toronto['latitude'], df_Toronto['longitude'], df_Toronto['Borough'], df_Toronto['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Toronto)  
    
map_Toronto

#### Define Foursquare Credentials and Version

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

In [49]:
CLIENT_ID = 'JDM0SDUZFOHLIGWTRF0NG0CEP3E3WFX1B1YQCTXISRS155ZX' # your Foursquare ID
CLIENT_SECRET = 'O0WTBPZXI5FUWPESAH01PJIZF4BW023A1YKGVPAX5RK5WCYO' # your Foursquare Secret
VERSION = '20180604' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JDM0SDUZFOHLIGWTRF0NG0CEP3E3WFX1B1YQCTXISRS155ZX
CLIENT_SECRET:O0WTBPZXI5FUWPESAH01PJIZF4BW023A1YKGVPAX5RK5WCYO


#### Let's create a function to get venues to all the neighborhoods in Toronto

In [0]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT = 100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        #print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        json_response = requests.get(url).json()
        #print(type(json_response["response"]['groups']))
        results = json_response["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Now run the getNearbyVenues function to all neighbourhood in Toronto city

In [51]:
toronto_venues = getNearbyVenues(names=df_Toronto['Neighbourhood'],
                                   latitudes=df_Toronto['latitude'],
                                   longitudes=df_Toronto['longitude']
                                  )

print('finish')

finish


#### Let's check the size of the resulting dataframe

In [52]:
print(toronto_venues.shape)
toronto_venues.head()

(5923, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Yorkville              43.671386              -79.390168   
1    Yorkville              43.671386              -79.390168   
2    Yorkville              43.671386              -79.390168   
3    Yorkville              43.671386              -79.390168   
4    Yorkville              43.671386              -79.390168   

                         Venue  Venue Latitude  Venue Longitude  \
0         Paramount Fine Foods       43.670677       -79.389865   
1   Four Seasons Hotel Toronto       43.671796       -79.389457   
2                       Pi Co.       43.670107       -79.389852   
3  Summer's Homemade Ice Cream       43.670903       -79.392299   
4                       Eataly       43.669754       -79.388720   

              Venue Category  
0  Middle Eastern Restaurant  
1                      Hotel  
2                Pizza Place  
3             Ice Cream Shop  
4               Gourmet Shop

Let's check how many venues were returned for each neighborhood

In [0]:
df_toronto_groupby_neighborhood = toronto_venues.groupby('Neighborhood').count()

In [76]:
df_toronto_groupby_neighborhood.sort_values(by=['Venue Category'], inplace=True, ascending=False)
df_toronto_groupby_neighborhood.head(20)

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                    
Yorkville                                  100                     100    100   
Toronto Dominion Centre                    100                     100    100   
Berczy Park                                100                     100    100   
Commerce Court                             100                     100    100   
Design Exchange                            100                     100    100   
First Canadian Place                       100                     100    100   
Grange Park                                100                     100    100   
Harbourfront                               100                     100    100   
Harbourfront East                          100                     100    100   
Harbourfront West                          100                     100    100   
Kensington Market                          100                     100    100   
King                                       100                     100    100   
King and Spadina                           100                     100    100   
Martin Grove                               100                     100    100   
Ryerson                                    100                     100    100   
South of Bloor                             100                     100    100   
Adelaide                                   100                     100    100   
Lawrence Heights                            92                      92     92   
Studio District                             92                      92     92   
Chinatown                                   89                      89     89   

                         Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                              
Yorkville                           100              100             100  
Toronto Dominion Centre             100              100             100  
Berczy Park                         100              100             100  
Commerce Court                      100              100             100  
Design Exchange                     100              100             100  
First Canadian Place                100              100             100  
Grange Park                         100              100             100  
Harbourfront                        100              100             100  
Harbourfront East                   100              100             100  
Harbourfront West                   100              100             100  
Kensington Market                   100              100             100  
King                                100              100             100  
King and Spadina                    100              100             100  
Martin Grove                        100              100             100  
Ryerson                             100              100             100  
South of Bloor                      100              100             100  
Adelaide                            100              100             100  
Lawrence Heights                     92               92              92  
Studio District                      92               92              92  
Chinatown                            89               89              89

#### Let's find out how many unique categories can be curated from all the returned venues

In [55]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 336 uniques categories.


## 3. Analyze Each Neighborhood

In [56]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
#fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
#toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()


Accessories Store  Afghan Restaurant  African Restaurant  Airport  \
0                  0                  0                   0        0   
1                  0                  0                   0        0   
2                  0                  0                   0        0   
3                  0                  0                   0        0   
4                  0                  0                   0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Argentinian Restaurant  \
0                    0             0         0                       0   
1                    0             0         0                       0   
2                    0             0         0                       0   
3                    0             0         0                       0   
4                    0             0         0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  Astrologer  \
0            0           0                    0                 0           0   
1            0           0                    0                 0           0   
2            0           0                    0                 0           0   
3            0           0                    0                 0           0   
4            0           0                    0                 0           0   

   Athletics & Sports  Auto Dealership  Auto Garage  Automotive Shop  \
0                   0                0            0                0   
1                   0                0            0                0   
2                   0                0            0                0   
3                   0                0            0                0   
4                   0                0            0                0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Basketball Stadium  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0                   0      0          0                0         0   
1                   0      0          0                0         0   
2                   0      0          0                0         0   
3                   0      0          0                0         0   
4                   0      0          0                0         0   

   Beer Garden  Beer Store  Belgian Restaurant  Big Box Store  Bike Shop  \
0            0           0                   0              0          0   
1            0           0                   0              0          0   
2            0           0                   0              0          0   
3            0           0                   0              0          0   
4            0           0                   0              0          0   

   Bike Trail  Bistro  Bookstore  Boutique  Bowling Alley  \
0           0       0          0         0              0   
1           0       0          0         0              0   
2           0       0          0         0              0   
3           0       0          0         0              0   
4           0       0          0         0              0   

   Brazilian Res

And let's examine the new dataframe size.

In [57]:
toronto_onehot.shape

(5923, 336)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [58]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Accessories Store  Afghan Restaurant  \
0                    Adelaide           0.000000           0.000000   
1                   Agincourt           0.000000           0.000000   
2             Agincourt North           0.000000           0.000000   
3              Albion Gardens           0.000000           0.000000   
4                   Alderwood           0.000000           0.000000   
5              Bathurst Manor           0.000000           0.000000   
6               Bathurst Quay           0.000000           0.000000   
7             Bayview Village           0.000000           0.000000   
8                 Berczy Park           0.000000           0.000000   
9                 Birch Cliff           0.000000           0.000000   
10          Bloordale Gardens           0.000000           0.000000   
11                   Brockton           0.000000           0.000000   
12                   CN Tower           0.000000           0.000000   
13                Cabbagetown           0.000000           0.000000   
14                  Cedarbrae           0.000000           0.000000   
15                  Chinatown           0.000000           0.000000   
16                   Christie           0.000000           0.000000   
17       Church and Wellesley           0.000000           0.011628   
18                   Clairlea           0.000000           0.000000   
19             Clarks Corners           0.000000           0.000000   
20                 Cliffcrest           0.000000           0.000000   
21                  Cliffside           0.000000           0.000000   
22             Cliffside West           0.000000           0.000000   
23                 Cloverdale           0.000000           0.000000   
24             Commerce Court           0.000000           0.000000   
25                 Davisville           0.000000           0.000000   
26           Davisville North           0.000000           0.000000   
27                  Deer Park           0.000000           0.000000   
28            Design Exchange           0.000000           0.000000   
29            Don Mills North           0.000000           0.000000   
30            Don Mills South           0.000000           0.000000   
31                Dorset Park           0.000000           0.000000   
32         Dovercourt Village           0.000000           0.000000   
33                  Downsview           0.000000           0.000000   
34          Downsview Central           0.000000           0.000000   
35             Downsview East           0.000000           0.000000   
36            Downsview North           0.000000           0.000000   
37        Downsview Northwest           0.000000           0.000000   
38             Downsview West           0.000000           0.000000   
39                   Dufferin           0.000000           0.000000   
40       East Birchmount Park           0.000000           0.000000   
41               East Toronto           0.000000           0.000000   
42                      Emery           0.000000           0.000000   
43                   Eringate           0.000000           0.000000   
44           Exhibition Place           0.000000           0.000000   
45                   Fairview           0.000000           0.000000   
46       First Canadian Place           0.000000           0.000000   
47            Flemingdon Park           0.000000           0.000000   
48          Forest Hill North           0.000000           0.000000   
49             Forest Hill SE           0.000000           0.000000   
50           Forest Hill West           0.000000           0.000000   
51            Garden District           0.000000           0.000000   
52                  Glencairn           0.000000           0.000000   
53                Golden Mile           0.014925           0.000000   
54                Grange Park           0.000000           0.000000   
55                  Guildwood           0

Let's confirm the new size

In [59]:
toronto_grouped.shape

(194, 336)

#### Let's print each neighborhood along with the top 5 most common venues

In [60]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
            venue  freq
0     Coffee Shop  0.08
1      Restaurant  0.06
2            Café  0.05
3       Gastropub  0.04
4  Cosmetics Shop  0.04


----Agincourt----
                   venue  freq
0     Chinese Restaurant  0.31
1   Hong Kong Restaurant  0.08
2       Asian Restaurant  0.08
3            Coffee Shop  0.08
4  Vietnamese Restaurant  0.08


----Agincourt North----
                venue  freq
0  Chinese Restaurant  0.07
1              Bakery  0.07
2      Discount Store  0.04
3         Pizza Place  0.04
4                Bank  0.04


----Albion Gardens----
                  venue  freq
0         Grocery Store  0.15
1        Hardware Store  0.08
2              Pharmacy  0.08
3            Beer Store  0.08
4  Caribbean Restaurant  0.08


----Alderwood----
            venue  freq
0     Pizza Place  0.25
1        Pharmacy  0.12
2  Sandwich Place  0.12
3     Coffee Shop  0.12
4    Skating Rink  0.12


----Bathurst Manor----
               venue  freq
0     Baseball Fie

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [0]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [62]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide           Coffee Shop            Restaurant   
1        Agincourt    Chinese Restaurant         Shopping Mall   
2  Agincourt North    Chinese Restaurant                Bakery   
3   Albion Gardens         Grocery Store           Video Store   
4        Alderwood           Pizza Place        Sandwich Place   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Café             Gastropub        Cosmetics Shop   
1  Cantonese Restaurant            Restaurant      Asian Restaurant   
2        Ice Cream Shop         Movie Theater            Taco Place   
3        Sandwich Place          Liquor Store        Hardware Store   
4           Coffee Shop                   Gym                   Pub   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Breakfast Spot   American Restaurant                 Hotel   
1           Coffee Shop         Train Station     Korean Restaurant   
2            Beer Store          Liquor Store   Sporting Goods Shop   
3           Coffee Shop  Fast Food Restaurant            Beer Store   
4              Pharmacy          Skating Rink     Electronics Store   

   9th Most Common Venue 10th Most Common Venue  
0              Bookstore              BBQ Joint  
1  Vietnamese Restaurant   Hong Kong Restaurant  
2     Frozen Yogurt Shop    Fried Chicken Joint  
3               Pharmacy    Fried Chicken Joint  
4    Empanada Restaurant   Ethiopian Restaurant

In [82]:
neighborhoods_venues_sorted

Cluster Labels              Neighborhood       1st Most Common Venue  \
0                 0                  Adelaide                 Coffee Shop   
1                 0                 Agincourt          Chinese Restaurant   
2                 0           Agincourt North          Chinese Restaurant   
3                 0            Albion Gardens               Grocery Store   
4                 0                 Alderwood                 Pizza Place   
5                 2            Bathurst Manor                  Playground   
6                 0             Bathurst Quay                 Coffee Shop   
7                 0           Bayview Village               Metro Station   
8                 0               Berczy Park                 Coffee Shop   
9                 2               Birch Cliff                        Park   
10                0         Bloordale Gardens           Convenience Store   
11                0                  Brockton                         Bar   
12                0                  CN Tower                       Hotel   
13                0               Cabbagetown                  Restaurant   
14                0                 Cedarbrae        Fast Food Restaurant   
15                0                 Chinatown                        Café   
16                0                  Christie           Korean Restaurant   
17                0      Church and Wellesley                 Coffee Shop   
18                0                  Clairlea           Convenience Store   
19                2            Clarks Corners           Convenience Store   
20                0                Cliffcrest              Ice Cream Shop   
21                0                 Cliffside              Breakfast Spot   
22                0            Cliffside West              Breakfast Spot   
23                0                Cloverdale                 Coffee Shop   
24                0            Commerce Court                 Coffee Shop   
25                0                Davisville            Sushi Restaurant   
26                0          Davisville North            Sushi Restaurant   
27                0                 Deer Park                 Coffee Shop   
28                0           Design Exchange                 Coffee Shop   
29                0           Don Mills North              Clothing Store   
30                0           Don Mills South              Clothing Store   
31                0               Dorset Park                       Plaza   
32                0        Dovercourt Village                        Café   
33                0                 Downsview               Metro Station   
34                0         Downsview Central               Metro Station   
35                0            Downsview East               Metro Station   
36                0           Downsview North               Metro Station   
37                0       Downsview Northwest               Metro Station   
38                0            Downsview West               Metro Station   
39                0                  Dufferin                         Bar   
40                0      East Birchmount Park               Grocery Store   
41                0              East Toronto       Performing Arts Venue   
42                0                     Emery        Fast Food Restaurant   
43                1                  Eringate                        Park   
44                0          Exhibition Place                  Theme Park   
45                0                  Fairview                 Coffee Shop   
46                0      First Canadian Place                 Coffee Shop   
47                0           Flemingdon Park                         Gym   
48                0         Forest Hill North                  Restaurant   
49                0            Forest Hill SE                  Restaurant   
50                0          Forest Hill West                  Bagel Shop   
5

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [63]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 2, 0, 0, 0, 2], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [64]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df_Toronto
toronto_merged.rename(columns={"Neighbourhood": "Neighborhood"}, inplace = True )

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Postcode          Borough      Neighborhood   latitude  longitude  \
0      M5R  Central Toronto         Yorkville  43.671386 -79.390168   
1      M3J       North York   York University  43.779242 -79.483559   
2      M2P       North York   York Mills West  43.744039 -79.406657   
3      M2L       North York        York Mills  43.744039 -79.406657   
4      M4C        East York  Woodbine Heights  43.699930 -79.319132   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             0.0                  Café            Restaurant   
1             0.0                Bakery           Gas Station   
2             0.0           Coffee Shop            Restaurant   
3             0.0           Coffee Shop            Restaurant   
4             0.0          Skating Rink        Cosmetics Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    Italian Restaurant              Boutique           Coffee Shop   
1     Martial Arts Dojo      Business Service           Yoga Studio   
2   Japanese Restaurant                   Pub       Thai Restaurant   
3   Japanese Restaurant                   Pub       Thai Restaurant   
4          Dance Studio    Athletics & Sports              Pharmacy   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                 Hotel                   Spa         Women's Store   
1   Filipino Restaurant               Exhibit    Falafel Restaurant   
2                   Gym  Gym / Fitness Center      Business Service   
3                   Gym  Gym / Fitness Center      Business Service   
4              Bus Stop                  Park           Event Space   

  9th Most Common Venue 10th Most Common Venue  
0        Clothing Store      French Restaurant  
1                  Farm         Farmers Market  
2        Sandwich Place          Burrito Place  
3        Sandwich Place          Burrito Place  
4               Exhibit     Falafel Restaurant

Finally, let's visualize the resulting clusters

In [83]:
import math

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

print(rainbow)

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['latitude'], toronto_merged['longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    if (math.isnan(cluster)):
      cluster = 0
      print('nan')
    cluster_int = int(cluster)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster_int-1],
        fill=True,
        fill_color=rainbow[cluster_int-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

['#8000ff', '#00b5eb', '#80ffb4', '#ffb360', '#ff0000']
nan
nan


## 5. Examine Clusters

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster. 

#### Cluster 1

In [85]:
cluster_0 = toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]
cluster_0

Borough              Neighborhood  Cluster Labels  \
0     Central Toronto                 Yorkville             0.0   
1          North York           York University             0.0   
2          North York           York Mills West             0.0   
3          North York                York Mills             0.0   
4           East York          Woodbine Heights             0.0   
5           East York          Woodbine Gardens             0.0   
6         Scarborough                    Woburn             0.0   
7          North York            Wilson Heights             0.0   
8          North York           Willowdale West             0.0   
9          North York          Willowdale South             0.0   
10         North York                Willowdale             0.0   
11        Scarborough           Wexford Heights             0.0   
12        Scarborough                   Wexford             0.0   
13               York                    Weston             0.0   
15        Scarborough                 West Hill             0.0   
17         North York          Victoria Village             0.0   
18   Downtown Toronto            Victoria Hotel             0.0   
19         North York               Upwood Park             0.0   
21   Downtown Toronto     University of Toronto             0.0   
22   Downtown Toronto             Union Station             0.0   
23   Downtown Toronto          Underground city             0.0   
24       West Toronto                   Trinity             0.0   
25   Downtown Toronto           Toronto Islands             0.0   
26   Downtown Toronto   Toronto Dominion Centre             0.0   
27          East York          Thorncliffe Park             0.0   
28          Etobicoke               Thistletown             0.0   
29          Etobicoke        The Queensway West             0.0   
30          Etobicoke        The Queensway East             0.0   
31          Etobicoke              The Kingsway             0.0   
32       West Toronto        The Junction South             0.0   
33               York        The Junction North             0.0   
34       East Toronto         The Danforth West             0.0   
35       East Toronto          The Beaches West             0.0   
36       East Toronto               The Beaches             0.0   
37    Central Toronto                 The Annex             0.0   
38        Scarborough             Tam O'Shanter             0.0   
40          Etobicoke                  Sunnylea             0.0   
41    Central Toronto           Summerhill West             0.0   
42    Central Toronto           Summerhill East             0.0   
43        Scarborough                  Sullivan             0.0   
44       East Toronto           Studio District             0.0   
47          Etobicoke              St. Phillips             0.0   
48   Downtown Toronto            St. James Town             0.0   
49   Downtown Toronto            St. James Town             0.0   
51          Etobicoke            South of Bloor             0.0   
52   Downtown Toronto             South Niagara             0.0   
53    Central Toronto                South Hill             0.0   
54               York               Silverthorn             0.0   
55          Etobicoke               Silverstone             0.0   
57        Scarborough  Scarborough Village West             0.0   
58        Scarborough       Scarborough Village             0.0   
59        Scarborough   Scarborough Town Centre             0.0   
60   Downtown Toronto                   Ryerson             0.0   
61               York                 Runnymede             0.0   
62       West Toronto                 Runnymede             0.0   
63          Etobicoke     Royal York South West             0.0   
64          Etobicoke     Royal York South East             0.0   
65        Scarborough                Rouge Hill             0.0   
67    Central Toronto                  Roselawn             0

In [86]:
cluster_0.shape

(162, 13)

#### Cluster 2

In [0]:
cluster_1 = toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

In [88]:
cluster_1

Borough       Neighborhood  Cluster Labels  \
20    Scarborough        Upper Rouge             1.0   
39   West Toronto            Swansea             1.0   
56     North York       Silver Hills             1.0   
66    Scarborough              Rouge             1.0   
77    Scarborough         Port Union             1.0   
83      Etobicoke     Old Mill South             1.0   
84      Etobicoke     Old Mill North             1.0   
165    North York     Northwood Park             1.0   
197     Etobicoke  Kingsview Village             1.0   
214     Etobicoke         Humber Bay             1.0   
235     Etobicoke           Eringate             1.0   

          1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
20                         Park  Fast Food Restaurant           Yoga Studio   
39                         Park              Bus Line        Pilates Studio   
56    Middle Eastern Restaurant                  Park              Festival   
66                         Park  Fast Food Restaurant           Yoga Studio   
77                         Park           Yoga Studio              Festival   
83                         Park         Metro Station                   Spa   
84                         Park         Metro Station                   Spa   
165                        Park        Baseball Field           Yoga Studio   
197                        Park           Yoga Studio              Festival   
214  Construction & Landscaping                  Park           Yoga Studio   
235                        Park           Yoga Studio              Festival   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
20               Festival  Ethiopian Restaurant           Event Space   
39            Yoga Studio  Ethiopian Restaurant           Event Space   
56   Ethiopian Restaurant           Event Space               Exhibit   
66               Festival  Ethiopian Restaurant           Event Space   
77   Ethiopian Restaurant           Event Space               Exhibit   
83    American Restaurant                 River           Yoga Studio   
84    American Restaurant                 River           Yoga Studio   
165              Festival           Event Space               Exhibit   
197  Ethiopian Restaurant           Event Space               Exhibit   
214              Festival  Ethiopian Restaurant           Event Space   
235  Ethiopian Restaurant           Event Space               Exhibit   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
20                Exhibit    Falafel Restaurant                  Farm   
39                Exhibit    Falafel Restaurant                  Farm   
56     Falafel Restaurant                  Farm        Farmers Market   
66                Exhibit    Falafel Restaurant                  Farm   
77     Falafel Restaurant                  Farm        Farmers Market   
83   Fast Food Restaurant  Ethiopian Restaurant           Event Space   
84   Fast Food Restaurant  Ethiopian Restaurant           Event Space   
165    Falafel Restaurant                  Farm        Farmers Market   
197    Falafel Restaurant                  Farm        Farmers Market   
214               Exhibit    Falafel Restaurant                  Farm   
235    Falafel Restaurant                  Farm        Farmers Market   

    10th Most Common Venue  
20          Farmers Market  
39          Farmers Market  
56    Fast Food Restaurant  
66          Farmers Market  
77    Fast Food Restaurant  
83                 Exhibit  
84                 Exhibit  
165   Fast Food Restaurant  
197   Fast Food Restaurant  
214         Farmers Market  
235   Fast Food Restaurant

In [89]:
cluster_1.shape

(11, 13)

#### Cluster 3

In [0]:
cluster_2 = toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

In [91]:
cluster_2

Borough              Neighborhood  Cluster Labels  \
14          Etobicoke                 Westmount             2.0   
68   Downtown Toronto                  Rosedale             2.0   
85          Etobicoke         Old Burnhamthorpe             2.0   
86        Scarborough                  Oakridge             2.0   
175   Central Toronto                Moore Park             2.0   
184         Etobicoke             Markland Wood             2.0   
188         East York                   Leaside             2.0   
190        North York       Lawrence Manor East             2.0   
191        North York            Lawrence Manor             2.0   
195         Etobicoke  Kingsway Park South West             2.0   
196         Etobicoke  Kingsway Park South East             2.0   
198         Etobicoke          King's Mill Park             2.0   
207       Scarborough                   Ionview             2.0   
210        North York                 Humberlea             2.0   
212        North York             Humber Summit             2.0   
216       Scarborough            Highland Creek             2.0   
218        North York                Henry Farm             2.0   
261       Scarborough            Clarks Corners             2.0   
275       Scarborough               Birch Cliff             2.0   
281        North York            Bathurst Manor             2.0   

    1st Most Common Venue       2nd Most Common Venue  \
14            Pizza Place                        Park   
68             Food Truck                  Playground   
85                Dog Run                 Flower Shop   
86         Ice Cream Shop           Convenience Store   
175                   Gym           Convenience Store   
184           Golf Course              Baseball Field   
188        Sandwich Place         Japanese Restaurant   
190     Electronics Store                        Bank   
191     Electronics Store                        Bank   
195              Bus Line               Metro Station   
196              Bus Line               Metro Station   
198                  Park               Metro Station   
207         Metro Station  Construction & Landscaping   
210     Convenience Store                Food Service   
212                Bakery         Empanada Restaurant   
216              Pharmacy  Construction & Landscaping   
218                Lawyer                Tennis Court   
261     Convenience Store                        Park   
275                  Park                    Gym Pool   
281            Playground           Convenience Store   

          3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
14                  Gas Station           Yoga Studio  Fast Food Restaurant   
68                   Bike Trail                  Park   Japanese Restaurant   
85                  Gas Station                  Park           Yoga Studio   
86                         Park          Dessert Shop              Bus Stop   
175                  Playground          Tennis Court        Farmers Market   
184                        Park             Piano Bar           Yoga Studio   
188           Convenience Store                  Park      Business Service   
190                  Kids Store                  Park       Doctor's Office   
191                  Kids Store                  Park       Doctor's Office   
195                        Park              Bus Stop              Festival   
196                        Park              Bus Stop              Festival   
198         American Restaurant                   Spa                 River   
207               Deli / Bodega      Business Service                  Park   
210              Baseball Field           Gas Station    Italian Restaurant   
212  Construction & Landscaping                  Park                   Gym   
216                        Park              Festival  Ethiopian Restaurant   
218                        Park           Yoga Studio     Electro

In [92]:
cluster_2.shape

(20, 13)

#### Cluster 4

In [69]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

Borough   Neighborhood  Cluster Labels       1st Most Common Venue  \
79  East York  Parkview Hill             3.0  Construction & Landscaping   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
79           Yoga Studio   Filipino Restaurant  Ethiopian Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
79           Event Space               Exhibit    Falafel Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
79                  Farm        Farmers Market   Fast Food Restaurant

#### Cluster 5

In [70]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

Borough   Neighborhood  Cluster Labels 1st Most Common Venue  \
46  Scarborough   Steeles East             4.0            Playground   
50    Etobicoke  South Steeles             4.0            Playground   

      2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
46  Health & Beauty Service           Yoga Studio  Fast Food Restaurant   
50  Health & Beauty Service           Yoga Studio  Fast Food Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
46   Empanada Restaurant  Ethiopian Restaurant           Event Space   
50   Empanada Restaurant  Ethiopian Restaurant           Event Space   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
46               Exhibit    Falafel Restaurant                   Farm  
50               Exhibit    Falafel Restaurant                   Farm